In [51]:
###This file is a demonstration of EHMM1 (https://doi.org/10.1016/j.aim.2025.110411) by Allen, Grove, Long and Tu
#### Running the first cell will precompute a few Hauptmodln as in Table 1 of EHMM1
#### A few demonstrations are provided
#### All equations and theorems labels are from the final version of EHMM

def fr(a): #fractional part of a
    return a-floor(a)
####
def ris(a,k): #rising factorial
    return prod(a+i for i in srange(k))
####
def Hyp(A,B,x,N):
    return sum(prod(ris(a,i) for a in A)/prod(ris(a,i) for a in B)*x^i for i in srange(N))
####

q=var('q')
N=100 ###################     N=100, can adjust this number to get more coefficients
R.<q>=PowerSeriesRing(QQ,N)
def eta(m): #note that leading term q^(1/24) is not included
    return prod((1-q^(m*n)) for n in srange(1,N))
##A list of Hauptmodln from EHMM, HauptTable pairs these with corresponding hypergeometric data
HauptTable=[]
t2=16*q*eta(1)^8*eta(4)^(16)/eta(2)^(24) #t_2 of Table 1, namely modular lambda (2\tau)
HauptTable.append([[[1/2,1/2],[1,1]],t2])
uu=-64*q*eta(2)^(24)/eta(1)^(24)  #u for \Gamma_0(2) in Table 1
HauptTable.append([[[1/2,1/2,1/2],[1,1,1]],uu])
t4=uu/(uu-1) #page 53, $t_4$ for \Gamma_0(2) 
HauptTable.append([[[1/4,3/4],[1,1]],t4])
t3=27*q*eta(3)^(12)/(eta(1)^(12)+27*q*eta(3)^(12)) #page 53, $t_3$ for \Gamma_0(3)
HauptTable.append([[[1/3,2/3],[1,1]],t3])
t6p=108*q*eta(1)^(12)*eta(3)^(12)/(eta(1)^(12)+27*q*eta(3)^(12))^2    #from Table 1 of EHMM 1 t_{6+}
HauptTable.append([[[1/2,1/3,2/3],[1,1,1]],t6p])
t4p=256*q*eta(1)^(24)*eta(2)^(24)/(eta(1)^(24)+64*q*eta(2)^(24))^2  #from Table 1 of EHMM 1 t_{4+}
HauptTable.append([[[1/2,1/4,3/4],[1,1,1]],t4p])
t6a=t6p/(t6p-1)  #swap 1 and infinity for t6p
Jinv=1728/j_invariant_qexp(N) #1728/j-invariant
HauptTable.append([[[1/2,1/6,5/6],[1,1,1]],Jinv])
t6=(-(1-Jinv)^(1/2)/2+1/2) # $t_6$, 4 lines above Proposition 7.1
HauptTable.append([[[1/6,5/6],[1,1]],t6])
HauptTable.append([[[1/3,1/3],[1,1]],t3/(t3-1)]) #related to [1/3,2/3],[1,1] by Pfaff transformation
HauptTable.append([[[2/3,2/3],[1,1]],t3/(t3-1)]) #related to [1/3,2/3],[1,1] by Pfaff transformation
####comment out the following to space computation time and memory, remove # to use
###########
##Weight 1/2 Jacobi theta
###########
#T3=sum(q^(n^2) for n in srange(-11,11)) #\theta_3
#T4=sum((-1)^n*q^(n^2) for n in srange(-11,11)) #\theta_4
###########
##weight-1 cubic theta
###########
#aprim=R((3*q*eta(9)^3+eta(1)^3)/eta(3))
#aa=sum(aprim[3*i]*q^i for i in srange(N/3)) #cubic theta a(\tau), weight 1
##Normalized Eisenstein series
#E2=1-24*sum(n*q^n/(1-q^n) for n in srange(1,20)); #print(E2.O(10))
#E4=240*eisenstein_series_qexp(4,100) #Constant term =1
#E6=-504*eisenstein_series_qexp(6,100)
###########
#Eisenstein series given under the tables on page 53
###########
#E22=E2-2*sum(E2[i]*q^(2*i) for i in srange(20))#E_{2,2} on page 53
#E23=E2-3*sum(E2[i]*q^(3*i) for i in srange(20))#E_{2,3} on page 53

###########
#Period function using Section 4.1 of [Memoirs] based on Jacobi sums
###########
def Jc(a,b,p): #a,b are in ZZ
    D=DirichletGroup(p)
    A1=D[(a)%(p-1)]
    B1=D[(b)%(p-1)]
    return sum(A1(t)*B1(1-t) for t in srange(p))
def BJ(i,j,p):
    G=DirichletGroup(p)
    return -G[j](-1)*Jc(i,(-j)%(p-1),p)
def PP(A,B,t,p):
    AA=[(a*(p-1))%(p-1) for a in A]
    BB=[(a*(p-1))%(p-1) for a in B]
    n=len(A)
    D=DirichletGroup(p)
    sgn=prod(D[AA[i]](-1)*D[BB[i]](-1) for i in srange(1,n))
    tt=[]
    for i in srange(p-1):
        tt.append( prod(BJ(AA[j]+i,(BB[j]+i)%(p-1),p) for j in srange(n))*D[i](t))# for i in srange(p-1)]
    return  sum(a for a in tt)*(-1)^(n)/(p-1)*sgn  
##################    
#Given HD^\flat={A,B} and (r,s), (optional, can also be determined internally from HD) modular function t, print HD and q-expansion of f_{HD}
##################
def EHMM(A,B,r,s,t=None): #expansion for modular form HD^\flat=\{A,B}, adding r to A, s to B, t is the Hauptmodul
    if t==None:
        for data in HauptTable:
            if [A,B]==data[0]:
                t=data[1]
    if t==None:
        print('Hypergeometric datum does not have corresponding Hauptmodul in Table 1')
        return()
    M=denominator(r)
    n=numerator(r)
    C=(t)[1]
    rmf=(((t/C/q)^(r-1)*(1-t)^(s-r-1)*Hyp(A,B,t,N)*diff(t,q)).O(N)/C) 
    tar=sum(rmf[i]*q^(M*i+n) for i in srange(N))
    A.append(r)
    B.append(s)
    return  A,B, tar 
##################    
#checking condition 2 of Theorem 2.1. If it holds, check (2.12) for the first few primes
##################
def CharTrace(A,B,r,s,t=None):
    if t==None:
        for data in HauptTable:
            if [A,B]==data[0]:
                t=data[1]
    if t==None:
        print('Hypergeometric datum does not have corresponding Hauptmodul in Table 1')
        return()
    ff=EHMM(A,B,r,s,t=None);A1=ff[0];B1=ff[1];fHD=ff[2]
    M=lcm(lcm([(a).denominator() for a in A1]),lcm([(a).denominator() for a in B1]))
    ga=sum(b for b in B1)-sum(a for a in A1)-1 #\gamma(\HD)
    C1=t[1]; #leading coeff of t
    L=[['p','MF. pth','P(HD;1)1/chi(C1)' , 'conclusion']]
    for p in primes(10*M):  #can adjust 10 to compute more MF's coefficients
      if p%M==1:
             D=DirichletGroup(p);chi=D[(p-1)*r]
             ss=(-1)^(len(A1)-1)*chi(C1)^(-1)*PP(A1,B1,1,p) # middle term of (2.1) of EHMM
             if ss not in ZZ:
                 return print('Condition 2 of Theorem 2.1 fails')
             else:
                 if ga==1:
                        Z=Zp(p,1)
                        #delta term from (6.3) of EHMM
                        delt=prod([Z(a).gamma() for a in B1])/prod([Z(a).gamma() for a in A1])
                        delt=delt*Z(r).gamma()*Z(s-r).gamma()/Z(s).gamma()*C1^((1-p)*r)
                        if (ZZ(delt%p)-1)==0: #extract the sign of delta
                             delsgn=1
                        if ZZ(delt%p)==p-1:
                            delsgn=-1
                        if (ss-fHD[p])*delsgn==p:
                            L.append([p , fHD[p] ,   ss ,   '(2.12) holds for', p])
                        else:
                            L.append([p , fHD[p] ,  ss ,  '(2.12) fails for',p ])
                 else:
                   if ss-fHD[p]==0:
                       L.append([p , fHD[p] ,  ss ,   '(2.12) holds for', p])
                   else:  
                        L.append([p , fHD[p] ,  ss ,   '(2.12) fails for', p])
    return L 

In [19]:
EHMM([1/2,1/3,2/3],[1,1,1],1/6,2/3) # The outcome indidate we get holomorphic modular forms which are likely cuspforms

([1/2, 1/3, 2/3, 1/6],
 [1, 1, 1, 2/3],
 q + 17*q^7 + 89*q^13 + 107*q^19 - 125*q^25 + 308*q^31 - 433*q^37 - 520*q^43 - 54*q^49 - 901*q^61 + 1007*q^67 - 271*q^73 + 503*q^79 + 1513*q^91 + 1853*q^97 - 19*q^103 - 646*q^109 - 1331*q^121 + 380*q^127 + 1819*q^133 - 3043*q^139 - 3709*q^151 - 3850*q^157 - 379*q^163 + 5724*q^169 - 2125*q^175 - 4699*q^181 + 5111*q^193 + 4373*q^199 - 2071*q^211 + 5236*q^217 - 3220*q^223 + 4466*q^229 + 4769*q^241 + 9523*q^247 - 7361*q^259 - 8101*q^271 - 4030*q^277 + 5600*q^283 - 4913*q^289 - 8840*q^301 + 10640*q^307 - 9109*q^313 - 11125*q^325 - 10891*q^331 + 12293*q^337 - 6749*q^343 + 1367*q^349 + 4590*q^361 + 9413*q^367 - 12601*q^373 + 14687*q^379 + 1190*q^397 + 27412*q^403 + 8297*q^409 - 6679*q^421 - 15317*q^427 - 2590*q^433 + 14924*q^439 + 12710*q^457 + 11969*q^463 + 17119*q^469 - 13375*q^475 - 38537*q^481 - 6103*q^487 - 15136*q^499 - 4607*q^511 - 11881*q^523 - 12167*q^529 + 1889*q^541 + 21293*q^547 + 8551*q^553 - 46280*q^559 - 23941*q^571 + 27323*q^577 + 32956*

In [12]:
EHMM([1/2,1/6,5/6],[1,1,1],1/3,5/6) # The outcome indidate we get holomorphic modular forms which are likely cuspforms, related to the previous one as they
#Their primtive data are the same. In terms of coefficients, we can see it from some coefficieitns such as 31 and 43 indicating they are both CM and are differed 
#by a cubic twist

([1/2, 1/6, 5/6, 1/3],
 [1, 1, 1, 5/6],
 q - 8*q^4 + 20*q^7 - 70*q^13 + 64*q^16 + 56*q^19 - 125*q^25 - 160*q^28 + 308*q^31 + 110*q^37 - 520*q^43 + 57*q^49 + 560*q^52 + 182*q^61 - 512*q^64 - 880*q^67 + 1190*q^73 - 448*q^76 + 884*q^79 - 1400*q^91 - 1330*q^97 + 1000*q^100 + 1820*q^103 - 646*q^109 + 1280*q^112 - 1331*q^121 - 2464*q^124 + 380*q^127 + 1120*q^133 + 2576*q^139 - 880*q^148 + 1748*q^151 - 3850*q^157 - 3400*q^163 + 2703*q^169 + 4160*q^172 - 2500*q^175 + 3458*q^181 - 1150*q^193 - 456*q^196 - 5236*q^199 - 4480*q^208 + 6032*q^211 + 6160*q^217 - 3220*q^223 + 4466*q^229 - 7378*q^241 - 1456*q^244 - 3920*q^247 + 4096*q^256 + 2200*q^259 + 7040*q^268 + 812*q^271 - 4030*q^277 + 5600*q^283 - 4913*q^289 - 9520*q^292)

In [13]:
EHMM([1/2,1/6,5/6],[1,1,1],1/3,1,Jinv) #When r and s are not chosen suitably, (namely only if we replace 5/6 in the previous
# example by 1, the coefficients grow much faster 

([1/2, 1/6, 5/6, 1/3],
 [1, 1, 1, 1],
 q - 296*q^4 + 9236*q^7 - 13197312*q^10 - 1438765126*q^13 - 1300420949696*q^16 - 390302615218120*q^19 - 204243715293806592*q^22 - 84157588392428150909*q^25 - 40152955563907734312736*q^28 - 18327825236252747470518988*q^31 - 8723444444385825084720463872*q^34 - 4142298035847725949997900246930*q^37 - 1997639005005794062953677592723456*q^40 - 968225226391056059718770965433444872*q^43 - 473113283826873770966848980187323629568*q^46 - 232417271130138849669535565443523635863495*q^49 - 114803435413969085434034249323372053635510032*q^52 - 56962998571953865597881924956564711213678886912*q^55 - 28382072990584135150083709315642491536427140751360*q^58)

In [14]:
EHMM([1/2,1/2,1/2],[1,1,1],1/2,1,uu) #Equation (1.5) of EHMM

([1/2, 1/2, 1/2, 1/2],
 [1, 1, 1, 1],
 q - 4*q^3 - 2*q^5 + 24*q^7 - 11*q^9 - 44*q^11 + 22*q^13 + 8*q^15 + 50*q^17 + 44*q^19 - 96*q^21 - 56*q^23 - 121*q^25 + 152*q^27 + 198*q^29 - 160*q^31 + 176*q^33 - 48*q^35 - 162*q^37 - 88*q^39)

In [15]:
EHMM([1/2,1/2],[1,1],1/4,3/4,t2) #Theorem 2.4 of EHMM

([1/2, 1/2, 1/4],
 [1, 1, 3/4],
 q + 2*q^5 - 7*q^9 - 14*q^13 + 18*q^17 + 32*q^21 - 21*q^25 - 14*q^29 + 16*q^33 - 30*q^37 - 14*q^41 - 14*q^45 - 15*q^49 + 66*q^53 + 48*q^57 + 82*q^61 - 28*q^65 - 160*q^69 + 66*q^73 - 32*q^77)

In [17]:
[EHMM([1/2,1/2],[1,1],i/8,1,t2) for i in [1,3,5,7]] #K2(i/8,1) of EHMM page 18

[([1/2, 1/2, 1/8],
  [1, 1, 1],
  q - 3*q^9 - 6*q^17 + 23*q^25 + 12*q^33 - 66*q^41 - 15*q^49 + 84*q^57 + 48*q^65 - 58*q^73 - 99*q^81 + 102*q^89 + 26*q^97 - 192*q^105 + 66*q^113 + 109*q^121 + 108*q^129 + 30*q^137 - 144*q^145 + 18*q^153),
 ([1/2, 1/2, 3/8],
  [1, 1, 1],
  q^3 - q^11 - 7*q^19 + 6*q^27 + 16*q^35 - 9*q^43 - 6*q^51 - 9*q^59 - 23*q^67 + 23*q^75 + 17*q^83 + 16*q^91 + 3*q^99 - 17*q^107 + 48*q^115 - 66*q^123 - 71*q^131 + 23*q^139 - 15*q^147 + 64*q^155),
 ([1/2, 1/2, 5/8],
  [1, 1, 1],
  q^5 + q^13 - 4*q^21 - 3*q^29 + q^37 - 3*q^45 + 13*q^53 + 13*q^61 - 12*q^69 + 4*q^77 - 6*q^85 - 16*q^93 + q^101 - 15*q^109 - 3*q^117 - 2*q^125 + 28*q^133 + 24*q^141 - 19*q^149 + 21*q^157),
 ([1/2, 1/2, 7/8],
  [1, 1, 1],
  q^7 + 3*q^15 + 3*q^23 + 4*q^31 + 3*q^39 - 6*q^47 - 3*q^55 - 3*q^63 - 15*q^71 - 2*q^79 - 9*q^87 - 21*q^95 + 5*q^103 + 3*q^111 - 6*q^119 + 8*q^127 + 18*q^135 - 3*q^143 + 19*q^151 + 39*q^159)]

In [267]:
CharTrace([1/2,1/2],[1,1],1/2,1,t2)

[['p', 'MF. pth', 'P(HD;1)1/chi(C1)', 'conclusion'],
 [3, 0, 0, '(2.12) holds for', 3],
 [5, -6, -6, '(2.12) holds for', 5],
 [7, 0, 0, '(2.12) holds for', 7],
 [11, 0, 0, '(2.12) holds for', 11],
 [13, 10, 10, '(2.12) holds for', 13],
 [17, -30, -30, '(2.12) holds for', 17],
 [19, 0, 0, '(2.12) holds for', 19]]

In [254]:
CharTrace([1/2,1/2,1/2],[1,1,1],1/12,1/12+1/2,uu)

[['p', 'MF. pth', 'P(HD;1)1/chi(C1)', 'conclusion'],
 [13, -14, -1, '(2.12) holds for', 13],
 [37, -266, -229, '(2.12) holds for', 37],
 [61, -546, -485, '(2.12) holds for', 61],
 [73, 630, 703, '(2.12) holds for', 73],
 [97, 1582, 1679, '(2.12) holds for', 97],
 [109, -334, -225, '(2.12) holds for', 109]]

In [255]:
CharTrace([1/2,1/3,2/3],[1,1,1],1/6,2/3,t6p)

Condition 2 of Theorem 2.1 fails


In [40]:
CharTrace([1/2,1/2,1/2],[1,1,1],1/24,1/24+1/2)

[['p', 'MF. pth', 'P(HD;1)1/chi(C1)', 'conclusion'],
 [73, -350, -423, '(2.12) holds for', 73],
 [97, 770, 673, '(2.12) holds for', 97],
 [193, 4230, 4037, '(2.12) holds for', 193]]